Импортируем нужные библиотеки.

In [1]:
import pandas as pd
import xgboost as xgb

Распакуйте архив с данными в папку,где находится этот jupyter notebook (baseline.ipynb). У вас будет папка data,  содержащая необходимые файлы. 

В данном соревновании перед вами ставится задача предсказания категории возраста, к которой принадлежит клиент банка, на основании его транзакций.
В обучающем наборе содержатся информация по транзакциям 30000 клиентов, она находится в файле **transactions_train.csv**. Правильная категория возраста для обучающего набора находится в файле **train_target.csv**.

Считаем данные по транзакциям и правильные ответы.

In [2]:
transactions_train=pd.read_csv('data/transactions_train.csv')

In [3]:
train_target=pd.read_csv('data/train_target.csv')

Посмотрим на данные.

In [4]:
transactions_train.head()

client_id  trans_date  small_group  amount_rur
0      33172           6            4      71.463
1      33172           6           35      45.017
2      33172           8           11      13.887
3      33172           9           11      15.983
4      33172          10           11      21.341

* client_id - уникальный идентификатор клиента
* trans_date - дата совершения транзакции
* small_group - категория покупки
* amount_rur - сумма транзакции

In [5]:
train_target.head(5)

client_id  bins
0      24662     2
1       1046     0
2      34089     2
3      34848     1
4      47076     3

* client_id - уникальный идентификатор клиента, соответствует полю client_id из транзакций
* bins - целевая переменная, которую нужно предсказать, это категория возраста клиента

Далее представлен простой вариант решения задачи. Вы можете решать соревнование используя совершенно другой подход.

Посчитаем по каждому клиенту самые простые аггрегационные признаки.

In [6]:
agg_features=transactions_train.groupby('client_id')['amount_rur'].agg(['sum','mean','std','min','max']).reset_index()

In [7]:
agg_features.head()

client_id        sum       mean         std    min       max
0          4  28404.121  39.450168   73.511624  0.043  1341.802
1          6  15720.739  21.535259   26.200397  0.045   315.781
2          7  53630.036  69.379089  253.261383  0.043  4505.971
3         10  34419.365  48.752642   63.191701  0.045   654.893
4         11  26789.404  32.991877  107.395139  0.388  2105.058

Посчитаем для каждого клиента количество транзакций по каждой категории.

In [8]:
counter_df_train=transactions_train.groupby(['client_id','small_group'])['amount_rur'].count()

In [9]:
cat_counts_train=counter_df_train.reset_index().pivot(index='client_id', \
                                                      columns='small_group',values='amount_rur')

In [10]:
cat_counts_train=cat_counts_train.fillna(0)

In [11]:
cat_counts_train.columns=['small_group_'+str(i) for i in cat_counts_train.columns]

In [12]:
cat_counts_train.head()

small_group_0  small_group_1  small_group_2  small_group_3  \
client_id                                                               
4                    0.0          447.0            1.0           44.0   
6                    2.0          397.0            0.0          172.0   
7                    2.0           79.0            5.0           27.0   
10                  12.0          309.0            1.0           71.0   
11                   2.0          423.0            0.0           59.0   

           small_group_4  small_group_5  small_group_6  small_group_7  \
client_id                                                               
4                   93.0            0.0            0.0            0.0   
6                   10.0            0.0            0.0            0.0   
7                   19.0            1.0            0.0            2.0   
10                  65.0            0.0            0.0            0.0   
11                  23.0            3.0            0.0            0.0   

           small_group_8  small_group_9       ...         small_group_192  \
client_id                                     ...                           
4                    1.0           13.0       ...                     0.0   
6                    0.0            6.0       ...                     0.0   
7                    1.0           39.0       ...                     0.0   
10                   3.0           19.0       ...                     0.0   
11                   0.0           10.0       ...                     0.0   

           small_group_193  small_group_195  small_group_196  small_group_197  \
client_id                                                                       
4                      0.0              0.0              0.0              0.0   
6                      0.0              0.0              0.0              0.0   
7                      0.0              0.0              0.0              0.0   
10                     0.0              0.0              0.0              0.0   
11                     0.0              0.0              0.0              0.0   

           small_group_198  small_group_199  small_group_200  small_group_202  \
client_id                                                                       
4                      0.0              0.0              0.0              0.0   
6                      0.0              0.0              0.0              0.0   
7                      0.0              0.0              0.0              0.0   
10                     0.0              0.0              0.0              0.0   
11                     0.0              0.0              0.0              0.0   

           small_group_203  
client_id                   
4                      0.0  
6                      0.0  
7                      0.0  
10                     0.0  
11                     0.0  

[5 rows x 202 columns]

Далее соединим все файлы в один датафрейм с таргетом.

In [13]:
train=pd.merge(train_target,agg_features,on='client_id')

In [14]:
train=pd.merge(train,cat_counts_train.reset_index(),on='client_id')

In [15]:
train.head()

client_id  bins        sum       mean         std    min       max  \
0      24662     2  30254.011  34.774725   72.037354  0.074  1227.314   
1       1046     0  42548.570  52.015367  106.540962  0.550  1210.506   
2      34089     2  26842.816  34.325852   59.927450  0.043   782.641   
3      34848     1  15773.126  16.160990   14.224936  0.043   109.590   
4      47076     3  12488.375  15.929050   35.473591  0.432   541.165   

   small_group_0  small_group_1  small_group_2       ...         \
0            0.0          174.0            2.0       ...          
1            1.0          187.0           61.0       ...          
2            0.0          372.0            0.0       ...          
3            0.0          359.0            1.0       ...          
4            0.0          378.0            0.0       ...          

   small_group_192  small_group_193  small_group_195  small_group_196  \
0              0.0              0.0              0.0              0.0   
1              0.0              0.0              0.0              0.0   
2              0.0              0.0              0.0              0.0   
3              0.0              0.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   small_group_197  small_group_198  small_group_199  small_group_200  \
0              0.0              0.0              0.0              0.0   
1              0.0              0.0              0.0              0.0   
2              0.0              0.0              0.0              0.0   
3              0.0              0.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   small_group_202  small_group_203  
0              0.0              0.0  
1              0.0              0.0  
2              0.0              0.0  
3              0.0              0.0  
4              0.0              0.0  

[5 rows x 209 columns]

Теперь подгрузим тестовые данные для того, чтобы сделать предсказание. Проделаем с ними те же самые манипуляции, как и с обучающими данными.

In [16]:
transactions_test=pd.read_csv('data/transactions_test.csv')

test_id=pd.read_csv('data/test.csv')

In [41]:
agg_features_test=transactions_test.groupby('client_id')['amount_rur'].agg(['sum','mean','std','min','max']).reset_index()

In [43]:
agg_features_test.head()

client_id        sum       mean         std    min       max
0          0  17036.127  19.163247   40.561700  0.065   595.339
1          1  34748.964  47.666617   89.489278  0.298  1181.221
2          2  51188.069  68.433247  152.093601  0.043  2837.682
3          3  47975.203  67.857430  318.651653  0.043  6135.652
4          5  20059.100  21.803370   34.258433  0.043   439.902
5          8  56077.096  64.754152  140.806402  0.603  1432.934
6          9  32317.239  36.270751   97.376195  0.043  2472.396
7         15  20394.051  20.558519   23.800658  0.432   243.099
8         16  24881.653  35.193286   82.298739  0.906  1401.336
9         21  23818.108  29.735466   75.615020  0.229  1341.481

In [44]:
counter_df_test=transactions_test.groupby(['client_id','small_group'])['amount_rur'].count()

In [45]:
cat_counts_test=counter_df_test.reset_index().pivot(index='client_id', columns='small_group',values='amount_rur')

In [46]:
cat_counts_test=cat_counts_test.fillna(0)

In [47]:
cat_counts_test.columns=['small_group_'+str(i) for i in cat_counts_test.columns]

In [48]:
cat_counts_test.head()

small_group_0  small_group_1  small_group_2  small_group_3  \
client_id                                                               
0                    0.0          226.0            1.0           36.0   
1                   30.0          326.0            0.0           40.0   
2                   21.0          242.0            1.0           50.0   
3                    0.0          156.0           83.0           48.0   
5                   16.0          398.0            1.0           23.0   
8                   29.0          296.0            9.0          114.0   
9                   35.0          222.0          110.0           60.0   
15                   0.0          398.0            0.0           29.0   
16                   0.0          288.0            2.0           21.0   
21                   0.0          185.0           25.0          246.0   

           small_group_4  small_group_5  small_group_6  small_group_7  \
client_id                                                               
0                    9.0            0.0            0.0            0.0   
1                   56.0            0.0            0.0            0.0   
2                   48.0            4.0            0.0            6.0   
3                   31.0            2.0            0.0            1.0   
5                   25.0            0.0            0.0            0.0   
8                   76.0            0.0            0.0            0.0   
9                   17.0            0.0            0.0            0.0   
15                  17.0            0.0            0.0            0.0   
16                  68.0            1.0            2.0            0.0   
21                  21.0            0.0            0.0            0.0   

           small_group_8  small_group_9       ...         small_group_192  \
client_id                                     ...                           
0                    2.0           20.0       ...                     0.0   
1                    0.0           60.0       ...                     0.0   
2                    1.0           21.0       ...                     0.0   
3                    2.0           27.0       ...                     0.0   
5                    5.0           29.0       ...                     0.0   
8                    2.0            9.0       ...                     0.0   
9                    3.0            6.0       ...                     0.0   
15                   0.0            9.0       ...                     0.0   
16                   0.0            6.0       ...                     0.0   
21                   2.0            9.0       ...                     0.0   

           small_group_193  small_group_194  small_group_195  small_group_196  \
client_id                                                                       
0                      0.0              0.0              0.0              0.0   
1                      0.0              0.0              0.0              0.0   
2                      0.0              0.0              0.0              0.0   
3                      0.0              0.0              0.0              0.0   
5                      0.0              0.0              0.0              0.0   
8                      0.0              0.0              0.0              0.0   
9                      0.0              0.0              0.0              0.0   
15                     0.0              0.0              0.0              0.0   
16                     0.0              0.0              0.0              0.0   
21                     0.0              0.0              0.0              0.0   

           small_group_197  small_group_198  small_group_200  small_group_201  \
client_id                                                                       
0                      0.0              0.0              0.0              0.0   
1                      0.0              0.0              0.0              0.0   
2                      0.0         

In [49]:
test=pd.merge(test_id,agg_features_test,on='client_id')

In [51]:
test=pd.merge(test,cat_counts_test.reset_index(),on='client_id')

В тесте не было некоторых категорий трат, поэтому для того, чтобы обучить модель, нам нужно объединить пространство признаков и train и test.

In [52]:
common_features=list(set(train.columns).intersection(set(test.columns)))

In [53]:
y_train=train['bins']
X_train=train[common_features]
X_test=test[common_features]

Обучим xgboost на текущих признаках.

In [54]:
param={'objective':'multi:softprob','num_class':4,'n_jobs':4,'seed':42}

In [55]:
%%time
model=xgb.XGBClassifier(**param,n_estimators=300)
model.fit(X_train,y_train)

CPU times: user 9min 9s, sys: 2.8 s, total: 9min 12s
Wall time: 2min 33s


Сделаем предсказание.

In [29]:
pred=model.predict(X_test)

In [30]:
pred

array([0, 2, 3, ..., 2, 2, 3])

На public лидерборде такое предсказание должно дать качество 0.6118.

### Подготовим файл для отправки в систему

In [90]:
submission = pd.DataFrame({'bins': pred}, index=test.client_id)
submission.head()

bins
client_id      
28571         0
27046         2
13240         3
19974         0
10505         1

Сохраняем прогноз на диск в папку submissions. Имя прогноза соответсвует дате и времени его создания, закодированными с помощью timestamp.

In [91]:
import time
import os

current_timestamp = int(time.time())
submission_path = 'submissions/{}.csv'.format(current_timestamp)

if not os.path.exists('submissions'):
    os.makedirs('submissions')

print(submission_path)
submission.to_csv(submission_path, index=True)

submissions/1573837933.csv


Теперь все готово! Можно отправлять решение.